# NOTEBOOK PARA TESTE DA SOLUÇÃO MANUFATURADA DE 2 ORDEM

#### IMPORTAÇÃO DAS BIBLIOTECAS

In [2]:
import numpy as np
from Classes.Discretizacao_teste import Discretizacao as disc
from Classes.Planeta import Planeta
from Classes.Splines import CubicSpline
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
import plotly.graph_objects as go
import plotly.express as px
import polars as pl 
import seaborn as sns
import os


#### OBTENÇÃO DA TABELA

In [3]:
T = 2 #COMPRIMENTO DO INTERVALO
dados = np.zeros((1,4))
discretizacao = disc()
np.set_printoptions(threshold=np.inf)
y = np.array([[0.0, 0.0]]*51212)

for i in range(1, 13):
    n = 2**i #numero de pontos na discretização
    h = T/n #tamanho do passo
    y_disc, t = discretizacao.converte(n, TBP = False)
    y_disc = y_disc[:,0]
    t = np.squeeze(t)
    y_real = discretizacao.exata_manufaturada(t)
    y_real = np.squeeze(y_real)
    erro = y_disc[-1] - y_real[-1]
    y[i-1] = y_disc[-1]
    if i == 1:
        ordem_p = 0
    else:
        ordem_p = np.log2(ultimo_erro/erro)
    ultimo_erro = erro
    dados = np.vstack([dados, [n, h, erro, ordem_p]])
    
df = pl.from_numpy(dados[1:], schema=["n", "h", "erro", "ordem_p"])

#### VISUALIZANDO SOLUÇÃO EXATA E DISCRETIZADA

In [4]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=y_real, name = "Exata",
                         line = {'dash': 'dash',   'color': 'black'}))
fig.add_trace(go.Scatter(x=t, y=y_disc[:], name = "Discretizada",
                         line = {'dash': 'dot',   'color': 'black'}))

fig.update_layout(title="Discretização", xaxis_title="t", yaxis_title="y", legend_title = "Legenda", width = 600)
fig.show()

### TABELA DE CONVERGÊNCIA PRA SOLUCAO MANUFATURADA

#### COM SOLUÇÃO EXATA E ORDEM P


In [5]:
df = df.select(pl.all().map_elements(lambda x: "{:.4e}".format(x)))
df.write_csv('Tabelas/tabela_convergencia_manufaturada_2_ordem.csv')
os.system("python tably.py Tabelas/tabela_convergencia_manufaturada_2_ordem.csv > Tabelas/tabela_convergencia_manufaturada_2_ordem.tex")

0

#### ORDEM COM DIFERENÇAS RELATIVAS

In [9]:
y_diff_rel = np.squeeze(np.log2(np.abs(y[0:-2] - y[1:-1])/np.abs(y[1:-1] - y[2:])))
y = np.squeeze(y)
pl.DataFrame({"y": y[0:-2], "y+1": y[1:-1], "y+2": y[2:], "y_diff_rel": y_diff_rel}).write_csv("Tabelas/tabela_convergencia_manufaturada_diff_rel.csv")

ComputeError: CSV format does not support nested data

#### MODELAGEM COM SPLINES CÚBICOS


In [ ]:
#SPLINE CUBICO
cs = CubicSpline(t, y_disc)

#intervalo de plotagem do spline 30 vezes mais preciso
t_spline = np.linspace(0, 2, 30*len(t))[0:-2]

# Create figure
fig = go.Figure()

# Add real values
fig.add_trace(go.Scatter(x=t_spline, y=cs(t_spline), mode='lines', name='Spline'))
fig.add_trace(go.Scatter(x=t, y=y_disc, mode='lines', name='Discretização'))
# Set layout
fig.update_layout(
    title='Movimento de tres bolas',
    xaxis_title='X (m)',
    yaxis_title='Y (m)',
    legend_title='Legend',
    showlegend=True
)

fig.show()

